In [1]:
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots


In [4]:
h_0 = 0.01

x_l = -1
x_r = 1

y_l = -1
y_r = 1

n_x = int((x_r - x_l)/h_0)
n_y = int((y_r - y_l)/h_0)

h_x = (x_r - x_l) / n_x
h_y = (y_r - y_l) / n_y

In [5]:
def exact_solution(x, y):
  return np.sinh(x + y) * np.sinh(y - x)

In [6]:
def mu_1(y):
  return np.sinh(y + 1) * np.sinh(y - 1)

In [7]:
def mu_2(x):
  return np.sinh(1 - x) * np.sinh(1 + x)

In [8]:
x = np.linspace(x_l + h_x / 2, x_r - h_x / 2, n_x)
y = np.linspace(y_l + h_y / 2, y_r - h_y / 2, n_y)

X, Y = np.meshgrid(x, y)

In [9]:
def OpL(u, h_x, h_y):
  res = 4 * u.copy()
  res[1:, :] += (u[1:, :] - u[:-1, :]) / h_x ** 2
  res[0, :] += 2 * u[0, :] / h_x ** 2
  res[:-1, :] += (u[:-1, :] - u[1:, :]) / h_x ** 2
  res[-1, :] += 2 * u[-1, :] / h_x ** 2
  res[:, 1:] += (u[:, 1:] - u[:, :-1]) / h_y ** 2
  res[:, 0] += 2 * u[:, 0] / h_y ** 2
  res[:, :-1] += (u[:, :-1] - u[:, 1:]) / h_y ** 2
  res[:, -1] += 2 * u[:, -1] / h_y ** 2
  return res

In [10]:
def right_side(x, y, h_x, h_y):
  res = np.zeros((len(x), len(y)))
  res[0, :] += 2 * mu_1(y) / h_x ** 2
  res[-1, :] += 2 * mu_1(y) / h_x ** 2
  res[:, 0] += 2 * mu_2(x) / h_y ** 2
  res[:, -1] += 2 * mu_2(x) / h_y ** 2
  return res

In [11]:

lx = x_r - x_l
ly = y_r - y_l


def graf(errors, t1, t2):
    fig = go.Figure()

    fig.add_trace(go.Scatter(x=list(range(len(errors))), y=errors ,mode='lines',line=dict(color='black')))

    fig.update_layout(
      width=1200,
      height=900,
      title={'text': f"Ошибка по итерациям, tau = {t1:.9f}, tau_max = {t2:.9f}",'x': 0.5,},
      xaxis=dict(type='log', title='Итерация',exponentformat='power'),
      yaxis=dict(type='log', title='Ошибка',exponentformat='power'),
    )

    fig.show()
    
    q_values = []
    
    for i in range(1, len(errors)):
        if errors[i-1] > 0: 
            q = errors[i] / errors[i-1]
            q_values.append(q)
    
    print(f"Оценка параметра q: {np.mean(q_values)}")
    

def simple_iteration_method(u, x, y, h_x, h_y, num, show_info = True, tol=1e-6):
    X, Y = np.meshgrid(x, y)
    exact_sol = exact_solution(X, Y).transpose()
    f = right_side(x, y, h_x, h_y)
    
    lambda_min = 4 / (h_x**2) * np.sin(np.pi * h_x / (2 * lx))**2 + \
                 4 / (h_y**2) * np.sin(np.pi * h_y / (2 * ly))**2
    lambda_max = 4 / (h_x**2) + 4 / (h_y**2)

    
    tau_max = 0.25 * h_x**2
    tau_list = [(2 / (lambda_min + lambda_max)), (1.5 / (lambda_min + lambda_max)), ( 1 / (lambda_min + lambda_max)), (0.24 * h_x**2), (0.5 * h_x**2)]
    
    tau_opt = tau_list[num]


    

    err = []
    err.append(np.linalg.norm(u - exact_sol))
    
    count_iter = 0
    
    while True:
        count_iter += 1
        if(count_iter > 30000):
            print("метод расходится")
            break
        
        
        Lu = OpL(u, h_x, h_y)
        u_new = u + tau_opt * (f - Lu) 
        
        err.append(np.linalg.norm(u_new - exact_sol))
        
        if np.linalg.norm(u_new - u) < tol:  
            break
        
        u = u_new       

    if show_info:
        graf(err, tau_opt, tau_max)
    

    

    return u_new.transpose()

u = np.zeros((n_x, n_y))

# 0 q = 0.9993770472730646 tau = 2/(lam_min + lam_max)
# 1 q = 0.9995215501677616 tau = 1.5/(lam_min + lam_max)
# 2 q = 0.9996704352092836 tau = 1/(lam_min + lam_max)
# 3 q = 0.9993998866587768 tau = 0.24 * h_0**2 (tay_max = 0.25 * h_0**2)
# 4 ---------------------- tau = 0.5 * h_0**2 (tay_max = 0.25 * h_0**2) метод расходится!
# при num = 0, имеем tau = tau_opt и как следствие - минимальный q, то есть лучшую сходимость

num = 0
num_sol = simple_iteration_method(u, x, y, h_x, h_y, num)

real_sol = exact_solution(X, Y)


Оценка параметра q: 0.9993770472730646


In [12]:


fig = make_subplots(
    rows=2, cols=1, 
    subplot_titles=("Численное решение", "Реальное решение"), 
    vertical_spacing=0.1  #
)

# Численное решение
fig.add_trace(go.Heatmap(
    z=num_sol,
    x=X[0],
    y=Y[:, 0],
    colorscale='hot',
    showscale=True,
    colorbar=dict(title="Численное решение", len=0.4, y=0.8),
), row=1, col=1)

# Точное решение
fig.add_trace(go.Heatmap(
    z=real_sol,
    x=X[0],
    y=Y[:, 0],
    colorscale='hot',
    showscale=True,
    colorbar=dict(title="Реальное решение", len=0.4, y=0.2),
), row=2, col=1)


fig.update_layout(
    title={'text': f"Сравнение графиков, h = {h_0}",'x': 0.5,},
    height=1400,  
    width=1200,   
)

fig.show()

In [16]:
diff = abs(num_sol - real_sol)
print(np.max(diff))

fig = go.Figure()


fig.add_trace(go.Heatmap(
    z=diff,
    x=X[0],
    y=Y[:, 0],
    colorscale='hot',  
    showscale=True,  
    colorbar=dict(title="Разница", len=0.6, exponentformat='power'),  # Настройка цветовой шкалы
))


fig.update_layout(
    title={'text': f"Абсолютная ошибка, h = {h_0}",'x': 0.5,},
    xaxis_title="x", 
    yaxis_title="y",  
    height=800,       
    width=1000,        
)



fig.show()

9.308417977660355e-05


In [15]:
diffs = []
hs = [0.5, 0.1, 0.05, 0.01]
for h in hs:
    
    x_l = -1
    x_r = 1
    
    y_l = -1
    y_r = 1

    n_x = int((x_r - x_l)/h)
    n_y = int((y_r - y_l)/h)

    h_x = (x_r - x_l) / n_x
    h_y = (y_r - y_l) / n_y


    x = np.linspace(x_l + h_x / 2, x_r - h_x / 2, n_x)
    y = np.linspace(y_l + h_y / 2, y_r - h_y / 2, n_y)

    X, Y = np.meshgrid(x, y)
    
    real_sol = exact_solution(X, Y)
    num_sol = simple_iteration_method(np.zeros((n_x, n_y)), x, y, h_x, h_y, 0, False)
    diff = np.abs(real_sol - num_sol)
    diffs.append(np.max(diff))



fig = go.Figure()

fig.add_trace(go.Scatter(x=hs, y=diffs,mode='lines+markers',line=dict(color='black'),marker=dict(color='red')))

fig.update_layout(
  width=1200,
  height=900,
  title={'text': "Оценка точности",'x': 0.5,},
  xaxis=dict(type='log', title='Шаг h',exponentformat='power'),
  yaxis=dict(type='log', title='Ошибка',exponentformat='power'),
)

fig.show()
